In [26]:
import plotly.express as px
import os
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import altair as alt
#alt.data_transformers.enable("vegafusion")
import math
from datetime import datetime, timedelta



#import csv
pd.set_option('display.max_rows', None)  # Display all rows

In [27]:
day = "11"
month = "10"
dataset = "ble"

base = -1
base_person = -1

date = day + "_" + month #change date accordingly
date_year = "2023-" + month + "-" + day
"""
if date == "11_10":
    base = 1
elif date == "13_10":
    base = 2
elif date == "24_08":
    base = 0
    base_person = 1
else:
    base = 0

if base == 1 or base ==2:
    folder_path = dataset + '_base/'
elif base_person == 1:
    folder_path = dataset + '_base_person/'
        """
folder_path = dataset +'_'+ date + '/'



def process_file(file_number, date):
    folder_path = dataset +'_'+ date + '/'
    file_path = os.path.join(folder_path, f'{dataset}_{date}_{file_number}.csv')
    print(file_path)
    if os.path.exists(file_path):
        df = pd.read_csv(file_path, parse_dates=['ts'])

        # Remove first empty column if it exists
        if df.shape[1] == 4:

            df = df.drop(df.columns[0], axis=1)
        # Keep entries with 'gabarit' equal to 1 or 2
        df_filt = df[(df['id'] == 2) | (df['id'] == 1)]
        df_filt = df_filt[(df_filt['rssi'] != 0)]

        # Write the updated DataFrame back to the CSV file
        df.to_csv(file_path, index = False)
        # Reset the index of the DataFrame
        df_filt = df_filt.reset_index(drop = True)

        return df_filt
    else:
        return pd.DataFrame

df1 = process_file(2,date)
df2 = process_file(1,date)
df3 = process_file(3,date)


ble_11_10/ble_11_10_2.csv
ble_11_10/ble_11_10_1.csv
ble_11_10/ble_11_10_3.csv


In [28]:
def plot_ble(df,station):
    # Plotly line graph
    color_discrete= {'1': 'tomato', '2': 'conrflowerblue'}

    fig = px.line(df, x='ts', y='rssi', color='id', color_discrete_map=color_discrete,
                  title=f'Line Graph for Station {station}')
    fig.update_layout(xaxis_title='Timestamp', yaxis_title='RSSI', legend_title='ID')
    fig.show()
plot_ble(df1,station =1)
plot_ble(df2, station =2)
plot_ble(df3, station = 3)



c:\Users\isacc\miniconda3\Lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



c:\Users\isacc\miniconda3\Lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



c:\Users\isacc\miniconda3\Lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [29]:
def analyse_df(df1, df2, df3, beacon):
    # Filter DataFrames for the given id value
    df1_id = df1[(df1['id'] == beacon)].reset_index(drop=True)
    df2_id = df2[(df2['id'] == beacon)].reset_index(drop=True)
    df3_id = df3[(df3['id'] == beacon)].reset_index(drop=True)


    # Combine dataframes with an outer merge
    merged_df = df1_id.merge(df2_id, on='ts', how='outer',suffixes = ['1','2']).merge(df3_id, on='ts', how='outer',suffixes = ['','3'])

    merged_df.drop(columns=['id1', 'id2', 'id'], inplace=True)
    merged_df.rename(columns={'rssi': 'rssi3'}, inplace=True)

    merged_df = merged_df.sort_values(by='ts')

    merged_df = merged_df.ffill()
    merged_df = merged_df.reset_index(drop=True)
    

    return merged_df


df_rssi1 = analyse_df(df1,df2,df3, beacon = 1) #beacon 1
df_rssi2 = analyse_df(df1,df2,df3, beacon = 2) #beacon 2

#print(df_rssi2)


In [30]:
# FIND BASE VALUES
def find_ref_ble_1_2(df_rssi1, df_rssi2):

    df_rssi1 = df_rssi1[(df_rssi1['rssi1'] != -100) & (df_rssi1['rssi2'] != -100) & (df_rssi1['rssi3'] != -100)]
    df_rssi2 = df_rssi2[(df_rssi2['rssi1'] != -100) & (df_rssi2['rssi2'] != -100) & (df_rssi2['rssi3'] != -100)]

    ref_values = np.zeros((3,3))
    #############################################################
    #                              station 1 station 2 station 3
    #beacon placed in station 1     X         X         X
    #beacon placed in station 2     X         X         X
    #beacon placed in station 3     X         X         X

    #beacon 2 placed in beggining (1)
    #beacon 1 placed in end on production line (2)
    med1_1 = df_rssi2['rssi1'].median()
    av1_1 = df_rssi2['rssi1'].mean()

    med2_1 = df_rssi2['rssi2'].median()
    av2_1 = df_rssi2['rssi2'].mean()

    med3_1 = df_rssi2['rssi3'].median()
    av_3_1 = df_rssi2['rssi3'].mean()

    print(med1_1, med2_1, med3_1)
    ref_values[0,:] = [av1_1,av2_1,av_3_1]

    med1_2 = df_rssi1['rssi1'].median()
    av1_2 = df_rssi1['rssi1'].mean()

    med2_2 = df_rssi1['rssi2'].median()
    av2_2 = df_rssi1['rssi2'].mean()

    med3_2 = df_rssi1['rssi3'].median()
    av_3_2 = df_rssi1['rssi3'].mean()

    #print(med1_2, med2_2, med3_2)
    ref_values[1,:] = [av1_2,av2_2,av_3_2]


    return ref_values

def find_ref_3(df_rssi1):
    df_rssi1 = df_rssi1[(df_rssi1['rssi1'] != -100) & (df_rssi1['rssi2'] != -100) & (df_rssi1['rssi3'] != -100)]

    # Filter DataFrame based on the time range
    med1_1 = df_rssi1['rssi1'].median()
    av1_1 = df_rssi1['rssi1'].mean()

    med2_1 = df_rssi1['rssi2'].median()
    av2_1 = df_rssi1['rssi2'].mean()

    med3_1 = df_rssi1['rssi3'].median()
    av_3_1 = df_rssi1['rssi3'].mean()

    #print(med1_1, med2_1, med3_1)
    ref_values[2,:] = [av1_1,av2_1,av_3_1]

    return ref_values

#if date == '11_10':
#    ref_values = find_ref_ble_1_2(df_rssi1, df_rssi2)
#    print(ref_values)
#elif date == '13_10':
#    ref_values = find_ref_3(df_rssi1)
#    print(ref_values)
#else:
ref_values=np.array(
[[-66.44549266, -74.26545582, -73.88842253],
 [-60.86128482, -43.43985976, -65.93448369],
 [-68.73783186, -56.43292456, -61.49354318]])




In [31]:
def state_df_person(df):
    #1 fim 18:02:00 -> 18:06:00
    #2 inicio 17:57:30 -> 18:01:00
    #3 monta cargas 18:07:00 -> 18:10:00
    df['real station'] = int(0)

    # Define the time frame
    start_time = pd.to_datetime('2023-08-24 17:57:35')
    end_time = pd.to_datetime('2023-08-24 18:00:40')

    # Set 'real station' to 2 for rows within the specified time frame
    df.loc[(df['ts'] >= start_time) & (df['ts'] <= end_time), 'real station'] = 1


    # Define the time frame
    start_time = pd.to_datetime('2023-08-24 18:02:00')
    end_time = pd.to_datetime('2023-08-24 18:05:20')

    # Set 'real station' to 1 for rows within the specified time frame
    df.loc[(df['ts'] >= start_time) & (df['ts'] <= end_time), 'real station'] = 2

    # Define the time frame
    start_time = pd.to_datetime('2023-08-24 18:07:00')
    end_time = pd.to_datetime('2023-08-24 18:10:00')

    # Set 'real station' to 3 for rows within the specified time frame
    df.loc[(df['ts'] >= start_time) & (df['ts'] <= end_time), 'real station'] = 3

    return df


if date == "24_08":
    #print(df_rssi2)
    df_rssi2 = state_df_person(df_rssi2)

if date == '11_10':
    df_rssi2['real station'] = 1
    df_rssi1['real station'] = 2
    
if date == '13_10':
    df_rssi2['real station'] = 3


print(ref_values)


[[-66.44549266 -74.26545582 -73.88842253]
 [-60.86128482 -43.43985976 -65.93448369]
 [-68.73783186 -56.43292456 -61.49354318]]


In [32]:
def calculate_rms(rssi, rssi_ref):
    # Calculate RMS difference for each receiver   
    rms_diff = np.sqrt(((rssi) - rssi_ref)**2)
    if math.isnan(rssi) or rssi == -100:
        rms_diff = 0

    return rms_diff

def define_weights(df_rssi, ref_values, iterations):
    # Create a DataFrame to store the results of different weight combinations
    results = pd.DataFrame(columns=['weight_station1', 'weight_station2', 'weight_station3', 'weight_rssi'])
    best_mean_accuracy  = 0 
    best_weights = None 

    # Iterate through weight combinations
    for w_station1 in np.linspace(0, 1, iterations):
        for w_station2 in np.linspace(0, 1, iterations):
            for w_station3 in np.linspace(0, 1, iterations):
                for w_rssi in np.linspace(0, 1, iterations):
                    

                    if w_station1 + w_station2 + w_station3 + w_rssi == 1:
              
                        #print("weights:", w_station1, w_station2, w_station3, w_rssi)
                        accuracies = []
                        for index, row in df_rssi.iterrows():
                            if row['real station'] == 0:
                                continue  # Skip rows with real station 0

                            # Calculate weighted RMS values for each station using reference values
                            rms_station = np.zeros(3)

                            for station in range(3):
                                rssi_values = [row['rssi1'], row['rssi2'], row['rssi3']]
                                
                                # Check for -100 or NaN in the rssi values
                                #if rssi_values[station] != -100 and not np.isnan(rssi_values[station]):
                                rms_station[station] = (w_station1 * calculate_rms(rssi_values[0], ref_values[station, 0]) + 
                                                        w_station2 * calculate_rms(rssi_values[1], ref_values[station, 1]) +
                                                        w_station3 * calculate_rms(rssi_values[2], ref_values[station, 2]))
                                #print("station  rms: ",station, rms_station)
                            #print()

                            # Determine the station with the minimum weighted RMS value
                            station_ref = np.argmin(rms_station) + 1

                            # Calculate the station determined by the smallest RSSI
                            station_rssi = np.argmax([row['rssi1'], row['rssi2'], row['rssi3']]) + 1
                            #print(row['rssi1'], row['rssi2'], row['rssi3'])
                            #print("max rssi: ", station_rssi)
                            # Calculate the weighted combination of station predictions
                            station_pred = int((w_station1 + w_station2 + w_station3) * station_ref + w_rssi * station_rssi)

                            if station_pred == row['real station']:
                                accuracies.append(1)
                            else:
                                accuracies.append(0)

                            #print("Station pred", station_pred)
                            #print("Real station", row['real station'])

                        mean_accuracy = sum(accuracies) / len(accuracies) *100
                        #print("Accuracy: ",mean_accuracy)
                        if mean_accuracy > best_mean_accuracy:
                            best_mean_accuracy = mean_accuracy
                            best_weights = {
                                'weight_station1': w_station1,
                                'weight_station2': w_station2,
                                'weight_station3': w_station3,
                                'weight_rssi': w_rssi,
                            }
                    else:
                        continue
    #best_weights = results.loc[results['error'].idxmin()]
 
    print(best_weights)
    return best_weights


def classify_points(df_rssi, best_weights, ref_values):
    confidence = 0.2

    for index, row in df_rssi.iterrows():
        # Calculate weighted RMS values for each station using reference values
        
        rms_station = np.zeros(3)

        #if index in range(0,10):
        #    print(f"i: {index}")

        for station in range(3):
            rms_station[station] = (
                best_weights['weight_station1'] * calculate_rms(row['rssi1'], ref_values[station, 0]) +
                best_weights['weight_station2'] * calculate_rms(row['rssi2'], ref_values[station, 1]) +
                best_weights['weight_station3'] * calculate_rms(row['rssi3'], ref_values[station, 2])
            )
            """
            if index in range(0,10):
                print(f"station: {station+1}")
                print(f"rssi1: {row['rssi1']}")
                print(calculate_rms(row['rssi1'], ref_values[station, 0]))
                print(f"rssi2: {row['rssi2']}")
                print(calculate_rms(row['rssi2'], ref_values[station, 1]))
                print(f"rssi3: {row['rssi3']}")
                print(calculate_rms(row['rssi3'], ref_values[station, 2]))
                print()"""

        #FALTA RMSS MIN
        #print(f"rms station: {rms_station}")
        # Determine the station with the minimum weighted RMS value
        station_ref = np.argmin(rms_station) + 1

        station_rssi = np.argmax([row['rssi1'], row['rssi2'], row['rssi3']]) + 1

        # Calculate the weighted combination of station predictions

        #print(f"min rssi: {min_rssi_station}")

        station_pred = station_rssi * best_weights['weight_rssi'] + station_ref * (1 - best_weights['weight_rssi'])
        #CONFIANCA estado 1-2 2-3
        if station_pred - round(station_pred) < confidence:
            station_pred = round(station_pred)
        else:

        station_pred = (round(station_pred))

        #if index in range(0,10):
        #    print(station_pred)

        #print()
        #print()
        df_rssi.loc[index, 'station'] = station_pred
        #int(station_pred)
     
    return df_rssi

def calculate_accuracy(df_rssi):
    accuracy = np.zeros(3)  # Initialize an array to store accuracy values for each station

    for station in range(1, 4):
        total_points = 0
        total_correct = 0

        for index, row in df_rssi.iterrows():
            if row['real station'] == 0:
                continue  # Skip rows with real station 0

            if row['real station'] == station:
                total_points += 1
                if row['station'] == row['real station']:
                    total_correct += 1

        # Calculate accuracy for the current station
        accuracy[station - 1] = total_correct / total_points * 100 if total_points > 0 else 0
    print("Accuracy: ",accuracy)
    return #accuracy


if date == '24_08':
    #print(df_rssi2)
    #df_rssi2['real station'] = df_rssi2['real station'].replace(3, 2)
    best_weights = define_weights(df_rssi2, ref_values, iterations=11)
    #print(best_weights)
    df_rssi2 = classify_points(df_rssi2,best_weights,ref_values)
    #df_rssi2['station'] = df_rssi2['station'].replace(3, 2)
    calculate_accuracy(df_rssi2)
    #print(df_rssi2)
else:
    best_weights = {
    'weight_station1': 0.0,
    'weight_station2': 0.1,
    'weight_station3': 0.2,
    'weight_rssi': 0.7
}

"""
if date == '11_10':
    #df_rssi2 = classify_points(df_rssi2,best_weights,ref_values)
    #calculate_accuracy(df_rssi2)

    df_rssi1 = classify_points(df_rssi1,best_weights,ref_values)
    calculate_accuracy(df_rssi1)
    #print(df_rssi1)

elif date == '13_10':
    df_rssi2 = classify_points(df_rssi2,best_weights,ref_values)
    calculate_accuracy(df_rssi2)
"""

print("Beacon 1")
df_rssi1 = classify_points(df_rssi1,best_weights,ref_values)
display(df_rssi1.loc[:10])
#display(df_rssi1)

print("Beacon 2")
df_rssi2 = classify_points(df_rssi2,best_weights,ref_values)
display(df_rssi2.loc[:10])


#print(ref_values)
#display(df_rssi2)



#[[-66.44549266 -74.26545582 -73.88842253]
# [-60.86128482 -43.43985976 -65.93448369]
# [-68.73783186 -56.43292456 -61.49354318]]
 

Beacon 1


ts  rssi1  rssi2  rssi3  real station  station
0  2023-10-11 09:00:10  -60.0    NaN    NaN             2      2.0
1  2023-10-11 09:00:22  -52.0    NaN    NaN             2      2.0
2  2023-10-11 09:00:28  -44.0    NaN    NaN             2      2.0
3  2023-10-11 09:00:33  -44.0  -73.0    NaN             2      2.0
4  2023-10-11 09:00:34  -60.0  -73.0    NaN             2      2.0
5  2023-10-11 09:00:39  -60.0  -67.0    NaN             2      2.0
6  2023-10-11 09:00:40  -48.0  -67.0    NaN             2      2.0
7  2023-10-11 09:00:46  -57.0  -67.0    NaN             2      2.0
8  2023-10-11 09:00:51  -57.0  -78.0    NaN             2      2.0
9  2023-10-11 09:00:58  -48.0  -78.0    NaN             2      2.0
10 2023-10-11 09:01:01  -48.0  -78.0  -76.0             2      1.0

Beacon 2


ts  rssi1  rssi2  rssi3  real station  station
0  2023-10-11 09:00:07    NaN    NaN  -69.0             1      1.0
1  2023-10-11 09:00:10  -71.0    NaN  -69.0             1      2.0
2  2023-10-11 09:00:15  -71.0 -100.0  -69.0             1      3.0
3  2023-10-11 09:00:19  -71.0 -100.0  -56.0             1      3.0
4  2023-10-11 09:00:21  -71.0  -65.0  -56.0             1      3.0
5  2023-10-11 09:00:33  -71.0  -73.0  -56.0             1      3.0
6  2023-10-11 09:00:37  -71.0  -73.0  -63.0             1      3.0
7  2023-10-11 09:00:39  -71.0  -60.0  -63.0             1      2.0
8  2023-10-11 09:00:43  -71.0  -60.0  -70.0             1      2.0
9  2023-10-11 09:00:51  -71.0  -50.0  -70.0             1      2.0
10 2023-10-11 09:00:52  -64.0  -50.0  -70.0             1      2.0

In [33]:
def remove_outliers(df):
    # Iterate through the DataFrame and update values
    for i in range(1, len(df) - 1):
        if df.at[i - 1, 'station'] == df.at[i + 1, 'station'] and df.at[i, 'station'] != df.at[i - 1, 'station']:
            df.at[i, 'station'] = df.at[i - 1, 'station']

    return df

def  remove_outliers2(df):
    # Iterate through the DataFrame and update values
    for i in range(1, len(df) - 2):
        if df.at[i - 1, 'station'] == df.at[i + 2, 'station'] and df.at[i, 'station'] == df.at[i + 1, 'station'] and df.at[i, 'station'] != df.at[i - 1, 'station']:
            df.at[i, 'station'] = df.at[i - 1, 'station']
            df.at[i + 1, 'station'] = df.at[i - 1, 'station']

    return df


#eliminiate_outliers(df_rssi1)
#print(df_rssi1)

df_rssi2 = remove_outliers(df_rssi2)
df_rssi2 = remove_outliers2(df_rssi2)
df_rssi1 = remove_outliers(df_rssi1)
df_rssi1 = remove_outliers2(df_rssi1)

#calculate_accuracy(df_rssi1)
#calculate_accuracy(df_rssi2)
#[96.77419355 81.81818182 88.23529412]

In [34]:

def time_in_station_ble(df_rssi):
    # Initialize time variables for each station
    time_in_1 = pd.to_timedelta('0 seconds')
    time_in_2 = pd.to_timedelta('0 seconds')
    time_in_3 = pd.to_timedelta('0 seconds')
    total_time = pd.to_timedelta('0 seconds')

    for index, row in df_rssi.iterrows():
        # Calculate time spent in each station based on station assignments
        if row['station'] == 1:
            if index == 0:
                continue
            time_in_1 += df_rssi.loc[index, 'ts'] - df_rssi.loc[index - 1, 'ts']

        if row['station'] == 2:
            if index == 0:
                continue
            time_in_2 += df_rssi.loc[index, 'ts'] - df_rssi.loc[index - 1, 'ts']

        if row['station'] == 3:
            if index == 0:
                continue
            time_in_3 += df_rssi.loc[index, 'ts'] - df_rssi.loc[index - 1, 'ts']

    print("time in each station", time_in_1,time_in_2,time_in_3)
    # Calculate total time and percentages for each station
    total_time = time_in_1 + time_in_2 + time_in_3
    perc1 = time_in_1 / total_time * 100
    perc1 = round(perc1, 2)
    perc2 = time_in_2 / total_time * 100
    perc2 = round(perc2, 2)
    perc3 = time_in_3 / total_time * 100
    perc3 = round(perc3, 2)
    #print("PREDICTED")
    print("time in each station", time_in_1,time_in_2,time_in_3)
    print("total time recorded:", time_in_1+time_in_2+time_in_3)
    print(f'station1: {perc1}%,    station2: {perc2}%,    station3: {perc3}%')
    return

def time_in_real_station_ble(df_rssi):
    # Initialize time variables for each station
    time_in_1 = pd.to_timedelta('0 seconds')
    time_in_2 = pd.to_timedelta('0 seconds')
    time_in_3 = pd.to_timedelta('0 seconds')

    for index, row in df_rssi.iterrows():
        # Calculate time spent in each station based on station assignments
        if row['real station'] == 1:
            if index == 0:
                continue
            time_in_1 += df_rssi.loc[index, 'ts'] - df_rssi.loc[index - 1, 'ts']

        if row['real station'] == 2:
            if index == 0:
                continue
            time_in_2 += df_rssi.loc[index, 'ts'] - df_rssi.loc[index - 1, 'ts']

        if row['real station'] == 3:
            if index == 0:
                continue
            time_in_3 += df_rssi.loc[index, 'ts'] - df_rssi.loc[index - 1, 'ts']

    # Calculate total time and percentages for each station
    total_time = time_in_1 + time_in_2 + time_in_3
    perc1 = time_in_1 / total_time * 100
    perc1 = round(perc1, 2)
    perc2 = time_in_2 / total_time * 100
    perc2 = round(perc2, 2)
    perc3 = time_in_3 / total_time * 100
    perc3 = round(perc3, 2)
    print("REAL")
    print("time in each station", time_in_1,time_in_2,time_in_3)
    print("total time recorded:", time_in_1+time_in_2+time_in_3)
    print(f'station1: {perc1}%,    station2: {perc2}%,    station3: {perc3}%')
    return


print("Beacon 1")
#print(df_rssi1)
time_in_station_ble(df_rssi1)
display(df_rssi1.loc[:10])
#display(df_rssi1)

print("Beacon 2")
time_in_station_ble(df_rssi2)
display(df_rssi2.loc[:10])






Beacon 1
time in each station 0 days 01:02:46 0 days 06:39:33 0 days 01:17:28
time in each station 0 days 01:02:46 0 days 06:39:33 0 days 01:17:28
total time recorded: 0 days 08:59:47
station1: 11.63%,    station2: 74.02%,    station3: 14.35%


ts  rssi1  rssi2  rssi3  real station  station
0  2023-10-11 09:00:10  -60.0    NaN    NaN             2      2.0
1  2023-10-11 09:00:22  -52.0    NaN    NaN             2      2.0
2  2023-10-11 09:00:28  -44.0    NaN    NaN             2      2.0
3  2023-10-11 09:00:33  -44.0  -73.0    NaN             2      2.0
4  2023-10-11 09:00:34  -60.0  -73.0    NaN             2      2.0
5  2023-10-11 09:00:39  -60.0  -67.0    NaN             2      2.0
6  2023-10-11 09:00:40  -48.0  -67.0    NaN             2      2.0
7  2023-10-11 09:00:46  -57.0  -67.0    NaN             2      2.0
8  2023-10-11 09:00:51  -57.0  -78.0    NaN             2      2.0
9  2023-10-11 09:00:58  -48.0  -78.0    NaN             2      2.0
10 2023-10-11 09:01:01  -48.0  -78.0  -76.0             2      1.0

Beacon 2
time in each station 0 days 00:38:49 0 days 05:55:13 0 days 02:25:46
time in each station 0 days 00:38:49 0 days 05:55:13 0 days 02:25:46
total time recorded: 0 days 08:59:48
station1: 7.19%,    station2: 65.81%,    station3: 27.0%


ts  rssi1  rssi2  rssi3  real station  station
0  2023-10-11 09:00:07    NaN    NaN  -69.0             1      1.0
1  2023-10-11 09:00:10  -71.0    NaN  -69.0             1      2.0
2  2023-10-11 09:00:15  -71.0 -100.0  -69.0             1      3.0
3  2023-10-11 09:00:19  -71.0 -100.0  -56.0             1      3.0
4  2023-10-11 09:00:21  -71.0  -65.0  -56.0             1      3.0
5  2023-10-11 09:00:33  -71.0  -73.0  -56.0             1      3.0
6  2023-10-11 09:00:37  -71.0  -73.0  -63.0             1      3.0
7  2023-10-11 09:00:39  -71.0  -60.0  -63.0             1      2.0
8  2023-10-11 09:00:43  -71.0  -60.0  -70.0             1      2.0
9  2023-10-11 09:00:51  -71.0  -50.0  -70.0             1      2.0
10 2023-10-11 09:00:52  -64.0  -50.0  -70.0             1      2.0

In [35]:
# Resampling with forward fill
def resample_df(df, freq):
    aux = 0
    # Set the 'Timestamp' column as the DataFrame index
    duplicates = df[df.duplicated(subset='ts', keep=False)]
    for index, row in duplicates.iterrows():
        if index % 2 == 0:
            df.at[index, 'ts'] = row['ts'] + timedelta(seconds=1)
            
    df = df.sort_values(by='ts')

    df.set_index('ts', inplace=True)

    # Resample the DataFrame with a desired frequency (e.g., 10 minutes) and forward fill
    resampled_df = df.resample(freq).ffill()

    # Reset the index to have the timestamp as a column again
    resampled_df = resampled_df.reset_index()

    return resampled_df

#start_time = pd.to_datetime(date_year + " 17:58:00")
#end_time = pd.to_datetime(date_year + " 18:10:01")
start_time = pd.to_datetime(date_year + " 09:00:00")
start_lunch = pd.to_datetime(date_year + " 13:00:00")
end_lunch = pd.to_datetime(date_year + " 14:00:00")
end_time = pd.to_datetime(date_year + " 18:00:00")


#df_rssi1_ = resample_df(df_rssi1,freq = '5S')
df_rssi1_resample = resample_df(df_rssi1,freq = '3S')
df_rssi2_resample = resample_df(df_rssi2,freq = '3S')

#morning
df1_morning = df_rssi1_resample[((df_rssi1_resample['ts'] >= start_time) & (df_rssi1_resample['ts'] <= start_lunch)) ]
#afternoon
df1_afternoon = df_rssi1_resample[((df_rssi1_resample['ts'] >= end_lunch) & (df_rssi1_resample['ts'] <= end_time))]
df1_morning = df1_morning.reset_index(drop=True)
df1_afternoon = df1_afternoon.reset_index(drop=True)


#morning
df2_morning = df_rssi2_resample[((df_rssi2_resample['ts'] >= start_time) & (df_rssi2_resample['ts'] <= start_lunch))] 
#afternoon
df2_afternoon = df_rssi2_resample[((df_rssi2_resample['ts'] >= end_lunch) & (df_rssi2_resample['ts'] <= end_time))]

df2_morning = df2_morning.reset_index(drop=True)
df2_afternoon = df2_afternoon.reset_index(drop=True)







In [36]:
def strip_plot(df,date, beacon, timeofday):
    df['ts'] = df['ts'].astype(str)  
    y_scale = alt.Scale(domain=[1, 2, 3])  # Set the y-axis range from 1 to 3
    # Define color encoding based on the station value
    color = alt.Color('station:N', scale=alt.Scale(
        domain=[1, 2, 3], range=['cornflowerblue', 'darkorange', 'violet'])
            , legend=alt.Legend(title='Station'))
    #else:
    #    y_scale = alt.Scale(domain=[1, 2])  # Set the y-axis range from 1 to 3
    #    color = alt.Color('station:N', scale=alt.Scale(
    #    domain=[1, 2], range=['cornflowerblue', 'darkorange']))

    # Custom ticks
    custom_x_ticks = [date_year + '09:00:00', date_year + '10:00:00', date_year + '11:00:00', date_year + '12:00:00', 
                      date_year + '13:00:00', date_year + '15:00:00', date_year + '16:00:00', date_year + '17:00:00', date_year + '18:00:00']    #1 inicio 17:57:30 -> 18:01:00
    # fim 18:02:00 -> 18:06:00
    #3 monta cargas 18:07:00 -> 18:10:00


    chart = alt.Chart(df).mark_tick().encode(
        x=alt.X('ts:T', timeUnit="hoursminutes", title='Timestamp'),#, axis=alt.Axis(values=custom_x_ticks)), # axis=alt.Axis(values=custom_x_ticks)),
        y=alt.Y('station:O', title='Station', scale=y_scale), 
        color=color  # Apply the color encoding
    ).properties(
        title=f'Classified station of beacon {beacon} in the {timeofday} ({date})',#,#{beacon}',
        width=400,  # Set the width to 600 pixels (adjust as needed)
        height=100  # Set the height to 400 pixels (adjust as needed)
    ).interactive()

    return chart

date_graph = day+ "-" + month + "-2023"

beacon1_morning = strip_plot(df1_morning, date_graph,beacon = 1, timeofday = 'morning')
beacon1_afternoon = strip_plot(df1_afternoon,date_graph, beacon = 1, timeofday = 'afternoon')

beacon2_morning = strip_plot(df2_morning, date_graph, beacon = 2, timeofday = 'morning')
beacon2_afternoon = strip_plot(df2_afternoon, date_graph,beacon = 2, timeofday = 'afternoon')
#chart2.show()

beacon1 = alt.hconcat(beacon1_morning, beacon1_afternoon)#.configure_tick(     bandSize=25)
beacon2 = alt.hconcat(beacon2_morning, beacon2_afternoon)#.configure_tick(    bandSize=25)

alt.vconcat(beacon1, beacon2).configure_tick(
    bandSize=25)

alt.VConcatChart(...)

alt.HConcatChart(...)

In [37]:
start_date = '11/10/2023'
end_date = '11/10/2023'

start_date = pd.to_datetime(start_date, format='%d/%m/%Y')
end_date = pd.to_datetime(end_date, format='%d/%m/%Y')

# Create a date range
date_range = pd.date_range(start=start_date, end=end_date)

for date in date_range:
    day = str(date.day).zfill(2)
    month = str(date.month).zfill(2)
    date_ = day + "_" + month
    print(date_)
    df1 = process_file(2,date_)
    if df1.empty:
        print("No data in this date")
        continue
    df2 = process_file(1,date_)
    df3 = process_file(3,date_)
    df_rssi1 = analyse_df(df1,df2,df3, beacon = 1) #beacon 1
    df_rssi2 = analyse_df(df1,df2,df3, beacon = 2) #beacon 2    
    ref_values=np.array(
    [[-66.44549266, -74.26545582, -73.88842253],
    [-60.86128482, -43.43985976, -65.93448369],
    [-68.73783186, -56.43292456, -61.49354318]])
    df_rssi1 = classify_points(df_rssi1,best_weights,ref_values)
    df_rssi2 = classify_points(df_rssi2,best_weights,ref_values)    
    df_rssi1 = remove_outliers(df_rssi1)
    df_rssi1 = remove_outliers2(df_rssi1)
    df_rssi2 = remove_outliers(df_rssi2)
    df_rssi2 = remove_outliers2(df_rssi2)

    start_time = pd.to_datetime(date_year + " 09:00:00")
    start_lunch = pd.to_datetime(date_year + " 13:00:00")
    end_lunch = pd.to_datetime(date_year + " 14:00:00")
    end_time = pd.to_datetime(date_year + " 18:00:00")

    df_rssi1_resample = resample_df(df_rssi1,freq = '3S')
    df_rssi2_resample = resample_df(df_rssi2,freq = '3S')
    display(df_rssi1_resample.loc[:30])

    #morning
    df1_morning = df_rssi1_resample[((df_rssi1_resample['ts'] >= start_time) & (df_rssi1_resample['ts'] <= start_lunch))]
    display(df1_morning.loc[:30])
    #afternoon
    df1_afternoon = df_rssi1_resample[((df_rssi1_resample['ts'] >= end_lunch) & (df_rssi1_resample['ts'] <= end_time))]
    df1_morning = df1_morning.reset_index(drop=True)
    df1_afternoon = df1_afternoon.reset_index(drop=True)
    #morning
    df2_morning = df_rssi2_resample[((df_rssi2_resample['ts'] >= start_time) & (df_rssi2_resample['ts'] <= start_lunch))] 
    #afternoon
    df2_afternoon = df_rssi2_resample[((df_rssi2_resample['ts'] >= end_lunch) & (df_rssi2_resample['ts'] <= end_time))]
    df2_morning = df2_morning.reset_index(drop=True)
    df2_afternoon = df2_afternoon.reset_index(drop=True)
    
    print("Beacon 1 morning")
    time_in_station_ble(df1_morning)
    print("Beacon 1 afternoon")
    time_in_station_ble(df1_afternoon)
    print("Beacon 2 morning")
    time_in_station_ble(df2_morning)
    print("Beacon 2 afternoon")
    time_in_station_ble(df2_afternoon)  
    
    beacon1_morning = strip_plot(df1_morning, date,beacon = 1, timeofday = 'morning')
    beacon1_afternoon = strip_plot(df1_afternoon,date, beacon = 1, timeofday = 'afternoon')

    beacon2_morning = strip_plot(df2_morning, date, beacon = 2, timeofday = 'morning')
    beacon2_afternoon = strip_plot(df2_afternoon, date,beacon = 2, timeofday = 'afternoon') 
      
    beacon1 = alt.hconcat(beacon1_morning, beacon1_afternoon)#.configure_tick(     bandSize=25)
    beacon2 = alt.hconcat(beacon2_morning, beacon2_afternoon)#.configure_tick(    bandSize=25)

    chart = alt.vconcat(beacon1, beacon2).configure_tick(bandSize=25)
    chart.display()
    

11_10
ble_11_10/ble_11_10_2.csv
ble_11_10/ble_11_10_1.csv
ble_11_10/ble_11_10_3.csv


ts  rssi1  rssi2  rssi3  station
0  2023-10-11 09:00:09    NaN    NaN    NaN      NaN
1  2023-10-11 09:00:12  -60.0    NaN    NaN      2.0
2  2023-10-11 09:00:15  -60.0    NaN    NaN      2.0
3  2023-10-11 09:00:18  -60.0    NaN    NaN      2.0
4  2023-10-11 09:00:21  -60.0    NaN    NaN      2.0
5  2023-10-11 09:00:24  -52.0    NaN    NaN      2.0
6  2023-10-11 09:00:27  -52.0    NaN    NaN      2.0
7  2023-10-11 09:00:30  -44.0    NaN    NaN      2.0
8  2023-10-11 09:00:33  -44.0  -73.0    NaN      2.0
9  2023-10-11 09:00:36  -60.0  -73.0    NaN      2.0
10 2023-10-11 09:00:39  -60.0  -67.0    NaN      2.0
11 2023-10-11 09:00:42  -48.0  -67.0    NaN      2.0
12 2023-10-11 09:00:45  -48.0  -67.0    NaN      2.0
13 2023-10-11 09:00:48  -57.0  -67.0    NaN      2.0
14 2023-10-11 09:00:51  -57.0  -78.0    NaN      2.0
15 2023-10-11 09:00:54  -57.0  -78.0    NaN      2.0
16 2023-10-11 09:00:57  -57.0  -78.0    NaN      2.0
17 2023-10-11 09:01:00  -48.0  -78.0    NaN      2.0
18 2023-10-11 09:01:03  -48.0  -78.0  -76.0      1.0
19 2023-10-11 09:01:06  -56.0  -78.0  -76.0      1.0
20 2023-10-11 09:01:09  -56.0  -63.0  -76.0      1.0
21 2023-10-11 09:01:12  -56.0  -63.0  -76.0      1.0
22 2023-10-11 09:01:15  -56.0  -63.0  -76.0      1.0
23 2023-10-11 09:01:18  -56.0  -63.0  -76.0      1.0
24 2023-10-11 09:01:21  -56.0  -63.0  -76.0      1.0
25 2023-10-11 09:01:24  -63.0  -63.0  -76.0      1.0
26 2023-10-11 09:01:27  -63.0  -63.0  -76.0      1.0
27 2023-10-11 09:01:30  -52.0  -63.0  -76.0      1.0
28 2023-10-11 09:01:33  -52.0  -63.0  -63.0      1.0
29 2023-10-11 09:01:36  -52.0  -63.0  -63.0      1.0
30 2023-10-11 09:01:39  -52.0  -63.0  -73.0      1.0

ts  rssi1  rssi2  rssi3  station
0  2023-10-11 09:00:09    NaN    NaN    NaN      NaN
1  2023-10-11 09:00:12  -60.0    NaN    NaN      2.0
2  2023-10-11 09:00:15  -60.0    NaN    NaN      2.0
3  2023-10-11 09:00:18  -60.0    NaN    NaN      2.0
4  2023-10-11 09:00:21  -60.0    NaN    NaN      2.0
5  2023-10-11 09:00:24  -52.0    NaN    NaN      2.0
6  2023-10-11 09:00:27  -52.0    NaN    NaN      2.0
7  2023-10-11 09:00:30  -44.0    NaN    NaN      2.0
8  2023-10-11 09:00:33  -44.0  -73.0    NaN      2.0
9  2023-10-11 09:00:36  -60.0  -73.0    NaN      2.0
10 2023-10-11 09:00:39  -60.0  -67.0    NaN      2.0
11 2023-10-11 09:00:42  -48.0  -67.0    NaN      2.0
12 2023-10-11 09:00:45  -48.0  -67.0    NaN      2.0
13 2023-10-11 09:00:48  -57.0  -67.0    NaN      2.0
14 2023-10-11 09:00:51  -57.0  -78.0    NaN      2.0
15 2023-10-11 09:00:54  -57.0  -78.0    NaN      2.0
16 2023-10-11 09:00:57  -57.0  -78.0    NaN      2.0
17 2023-10-11 09:01:00  -48.0  -78.0    NaN      2.0
18 2023-10-11 09:01:03  -48.0  -78.0  -76.0      1.0
19 2023-10-11 09:01:06  -56.0  -78.0  -76.0      1.0
20 2023-10-11 09:01:09  -56.0  -63.0  -76.0      1.0
21 2023-10-11 09:01:12  -56.0  -63.0  -76.0      1.0
22 2023-10-11 09:01:15  -56.0  -63.0  -76.0      1.0
23 2023-10-11 09:01:18  -56.0  -63.0  -76.0      1.0
24 2023-10-11 09:01:21  -56.0  -63.0  -76.0      1.0
25 2023-10-11 09:01:24  -63.0  -63.0  -76.0      1.0
26 2023-10-11 09:01:27  -63.0  -63.0  -76.0      1.0
27 2023-10-11 09:01:30  -52.0  -63.0  -76.0      1.0
28 2023-10-11 09:01:33  -52.0  -63.0  -63.0      1.0
29 2023-10-11 09:01:36  -52.0  -63.0  -63.0      1.0
30 2023-10-11 09:01:39  -52.0  -63.0  -73.0      1.0

Beacon 1 morning
time in each station 0 days 00:42:39 0 days 02:48:27 0 days 00:28:45
time in each station 0 days 00:42:39 0 days 02:48:27 0 days 00:28:45
total time recorded: 0 days 03:59:51
station1: 17.78%,    station2: 70.23%,    station3: 11.99%
Beacon 1 afternoon
time in each station 0 days 00:19:54 0 days 03:06:57 0 days 00:33:06
time in each station 0 days 00:19:54 0 days 03:06:57 0 days 00:33:06
total time recorded: 0 days 03:59:57
station1: 8.29%,    station2: 77.91%,    station3: 13.79%
Beacon 2 morning
time in each station 0 days 00:26:30 0 days 02:28:36 0 days 01:04:48
time in each station 0 days 00:26:30 0 days 02:28:36 0 days 01:04:48
total time recorded: 0 days 03:59:54
station1: 11.05%,    station2: 61.94%,    station3: 27.01%
Beacon 2 afternoon
time in each station 0 days 00:17:12 0 days 02:23:21 0 days 01:19:21
time in each station 0 days 00:17:12 0 days 02:23:21 0 days 01:19:21
total time recorded: 0 days 03:59:54
station1: 7.17%,    station2: 59.75%,    station3: 3

alt.VConcatChart(...)

In [38]:
def strip_plot(df,include_3):
    df['ts'] = df['ts'].astype(str)  
    if include_3:
        y_scale = alt.Scale(domain=[1, 2, 3])  # Set the y-axis range from 1 to 3
        # Define color encoding based on the station value
        color = alt.Color('real station:N', scale=alt.Scale(
            domain=[1, 2, 3], range=['cornflowerblue', 'darkorange', 'violet'])
             , legend=alt.Legend(title='Station'))
    else:
        y_scale = alt.Scale(domain=[1, 2])  # Set the y-axis range from 1 to 3
        color = alt.Color('real station:N', scale=alt.Scale(
        domain=[1, 2], range=['cornflowerblue', 'darkorange']))


    #x_domain = [pd.to_datetime(f'{date_year} 17:57:00'), pd.to_datetime(f'{date_year} 18:10:00')]
    custom_x_ticks = ['2023-08-24 17:58:00', '2023-08-24 18:00:00', '2023-08-24 18:02:00', '2023-08-24 18:04:00', '2023-08-24 18:06:00', '2023-08-24 18:08:00', '2023-08-24 18:10:00']    #1 inicio 17:57:30 -> 18:01:00

    #1 inicio 17:57:30 -> 18:01:00
    # fim 18:02:00 -> 18:06:00
    #3 monta cargas 18:07:00 -> 18:10:00

    chart = alt.Chart(df).mark_tick().encode(
        x=alt.X('ts:T', title='Timestamp', axis=alt.Axis(values=custom_x_ticks)),
        y=alt.Y('real station:O', title='Station'),#, scale=y_scale),
        color=color  # Apply the color encoding
    ).properties(
        title=f'Real station of beacon',#{beacon}',
        width=400,  # Set the width to 600 pixels (adjust as needed)
        height=100  # Set the height to 400 pixels (adjust as needed)
    ).configure_tick(
    #thickness=5,
    bandSize=25,)

    return chart


#display(df_rssi2_resample)
    
#chart1 = strip_plot(df_rssi1_,beacon=1)
#chart2 = strip_plot(df_rssi2_resample.loc[df_rssi2_resample['real station'] != 0],include_3=1)

#chart1 | 
#display(df_rssi2_resample[df_rssi2_resample['real station'] != 0])
#chart2

This section now gathers the data from all dates